<a href="https://colab.research.google.com/github/esmanursaracbasi/Calculation-of-the-relationship-between-job-advertisements-and-CV-s-with-using-TF-IDF/blob/master/nlp_job_cv_relationship.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import re
import numpy as np
import pandas as pd
from pprint import pprint

In [ ]:
from google.colab import files 
import io
uploaded = files.upload()

Saving cv_list.xlsx to cv_list.xlsx


In [ ]:
#data importation cv_list
column_names = ["RefNumber", "Resume" , "Yetenekler", "ResumeAll"]
cv_list_excel_path = "cv_list.xlsx"
cv_list_data = pd.read_excel(cv_list_excel_path) 
cv_list_df = pd.concat([cv_list_data]).reset_index().drop("index", axis=1)

In [ ]:
df= cv_list_df
df.head()

Unnamed: 0  ...                                          ResumeAll
0           0  ...  - Mapco ve TurkcellGroup bünyesindeki şirketle...
1           1  ...  <p>Aile şirketimizde ve inşaat sektöründe paza...
2           2  ...  Bilgi İşlem Yöneticisi.&nbsp;Moda Tekstil, Rot...
3           3  ...  - Setting up departments in the production fac...
4           4  ...  <p>İç Satın alma faaliyetlerinden sorumlu Satı...

[5 rows x 5 columns]

In [ ]:
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

In [ ]:
data = df.ResumeAll.values.tolist()

In [ ]:
# Tokenization and removing puntuations from values in list.
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True)) # deacc=True removes punctuations
        
data_words = list(sent_to_words(data)) # data_words is a list that inclues lists of values with cleaned form.

In [ ]:
print(data_words[:1]) #list in list and each list includes the sentences in a row. 

[['mapco', 've', 'turkcellgroup', 'bunyesindeki', 'sirketlerin', 'ms', 'backoffice', 'server', 'exchange', 'isa', 'sql', 've', 'client', 'kurulum', 'bakım', 'tamiri', 'civarı', 'pc', 'server', 've', 'cevre', 'birimleri', 'yazıcı', 'scanner', 'vs', 'br', 'pc', 've', 'cevre', 'birimlerinin', 'ayakta', 'tutulması', 'kullanıcılara', 'destek', 'verilmesi', 'br', 'lan', 've', 'wan', 'kontrolu', 'networkun', 'hata', 'raporlaması', 've', 'performans', 'iyilestirmesi', 'br', 'inet', 'mail', 've', 'dıs', 'network', 'baglantılarının', 'ayakta', 'tutulması', 'superonline', 've', 'turkcell', 'data', 'center', 'da', 'bulunan', 'microsoft', 'intel', 'microsoft', 'backoffice', 'small', 'backoffice', 'ms', 'office', 'windows', 'isletim', 'sistemleri', 'server', 'client', 'network', 'kablolama', 'server', 'access', 'linux', 'proxy', 'firewall', 'client', 'hp', 'dell', 'windows', 'isletim', 'active', 'directory', 'exchange', 'isa', 'cisco', 'cihazlar', 'wireless', 'network', 'adsl', 'microsoft', 'backoff

In [ ]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [ ]:
# showing and adding stopwords
from nltk.corpus import stopwords
stop_words = set(stopwords.words('turkish'))
new_stop_words=['aa','ul', 'li', 'r', 'span', 'br','u','h1','h2','h3','div','dir','em','strong','p','class','p','style','nbsp','text-align']
for i in new_stop_words:
  stop_words.add(i)

print(stop_words)

{'ama', 'ile', 'belki', 'birşey', 've', 'em', 'tüm', 'p', 'de', 'daha', 'ki', 'ne', 'niye', 'kim', 'nasıl', 'br', 'ya', 'birkaç', 'text-align', 'niçin', 'diye', 'siz', 'mu', 'aa', 'kez', 'çok', 'en', 'yani', 'da', 'hem', 'nbsp', 'hepsi', 'biz', 'eğer', 'mü', 'strong', 'çünkü', 'bu', 'için', 'bazı', 'nerde', 'aslında', 'gibi', 'nereye', 'div', 'style', 'hep', 'ise', 'ul', 'mı', 'h1', 'nerede', 'veya', 'u', 'h2', 'li', 'dir', 'hiç', 'h3', 'biri', 'neden', 'şey', 'class', 'acaba', 'o', 'her', 'r', 'az', 'span', 'şu', 'sanki', 'defa'}


In [ ]:
# removing stopwords 
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]
# Remove Stop Words
data_words_nostops = remove_stopwords(data_words)

In [ ]:
print(data_words_nostops[:1])

[['mapco', 'turkcellgroup', 'bunyesindeki', 'sirketlerin', 'ms', 'backoffice', 'server', 'exchange', 'isa', 'sql', 'client', 'kurulum', 'bakım', 'tamiri', 'civarı', 'pc', 'server', 'cevre', 'birimleri', 'yazıcı', 'scanner', 'vs', 'pc', 'cevre', 'birimlerinin', 'ayakta', 'tutulması', 'kullanıcılara', 'destek', 'verilmesi', 'lan', 'wan', 'kontrolu', 'networkun', 'hata', 'raporlaması', 'performans', 'iyilestirmesi', 'inet', 'mail', 'dıs', 'network', 'baglantılarının', 'ayakta', 'tutulması', 'superonline', 'turkcell', 'data', 'center', 'bulunan', 'microsoft', 'intel', 'microsoft', 'backoffice', 'small', 'backoffice', 'ms', 'office', 'windows', 'isletim', 'sistemleri', 'server', 'client', 'network', 'kablolama', 'server', 'access', 'linux', 'proxy', 'firewall', 'client', 'hp', 'dell', 'windows', 'isletim', 'active', 'directory', 'exchange', 'isa', 'cisco', 'cihazlar', 'wireless', 'network', 'adsl', 'microsoft', 'backoffice', 'small', 'backoffice', 'ms', 'office', 'windows', 'isletim', 'sist

note: I have tried some stopwords from diffrent sources but it is the most proper one I guess.

In [ ]:
# Creating corpus
corpus =[]
for doc in data_words_nostops: 
  corpus.append(" ".join(doc))

In [ ]:
array_corpus= np.array(corpus)

In [ ]:
df_cv_id =  df[['RefNumber']] # geting only cv_id from the dataframe
df_cv_id.head()

RefNumber
0        473
1        900
2       1323
3       3748
4       6363

In [ ]:
df_nostops = pd.DataFrame(corpus)

In [ ]:
df_cvID_skills = pd.concat([df_cv_id, df_nostops], axis=1)
df_cvID_skills.columns = ['cv_id' , 'skills']

In [ ]:
df_cvID_skills.head()  # this dataframe includes cvid and cleaned text.

cv_id                                             skills
0    473  mapco turkcellgroup bunyesindeki sirketlerin m...
1    900  aile sirketimizde insaat sektorunde pazarlama ...
2   1323  bilgi islem yoneticisi moda tekstil roteks tek...
3   3748  setting up departments in the production facil...
4   6363  ic satın alma sorumlu satın alma muduru olarak...

In [ ]:
#Convert a collection of text documents to a matrix of token counts
from sklearn.feature_extraction.text import CountVectorizer
vectorizer_cv = CountVectorizer()
bag_1 = vectorizer_cv.fit_transform(array_corpus)

In [ ]:
print(vectorizer_cv.vocabulary_) #A mapping of terms to feature indices.
print(vectorizer_cv.get_feature_names())

{'mapco': 47349, 'turkcellgroup': 75952, 'bunyesindeki': 11795, 'sirketlerin': 67228, 'ms': 50231, 'backoffice': 6865, 'server': 65997, 'exchange': 24825, 'isa': 36579, 'sql': 68792, 'client': 14564, 'kurulum': 44305, 'bakım': 7212, 'tamiri': 71633, 'civarı': 14400, 'pc': 57065, 'cevre': 13848, 'birimleri': 10010, 'yazıcı': 82390, 'scanner': 64808, 'vs': 79770, 'birimlerinin': 10019, 'ayakta': 6355, 'tutulması': 76242, 'kullanıcılara': 43806, 'destek': 18372, 'verilmesi': 79089, 'lan': 45026, 'wan': 79884, 'kontrolu': 42706, 'networkun': 51855, 'hata': 31973, 'raporlaması': 60950, 'performans': 57296, 'iyilestirmesi': 37859, 'inet': 35781, 'mail': 46756, 'dıs': 21320, 'network': 51842, 'baglantılarının': 6956, 'superonline': 69998, 'turkcell': 75948, 'data': 16752, 'center': 13607, 'bulunan': 11585, 'microsoft': 49100, 'intel': 36158, 'small': 67642, 'office': 52973, 'windows': 80252, 'isletim': 37019, 'sistemleri': 67360, 'kablolama': 38398, 'access': 191, 'linux': 45736, 'proxy': 601

In [ ]:
print(bag_1.toarray())
print(bag_1.shape)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
(8012, 85217)


In [ ]:
#Convert a collection of raw documents to a matrix of TF-IDF features.
from sklearn.feature_extraction.text import TfidfTransformer
tfidf = TfidfTransformer(use_idf=True, 
                         norm='l2', 
                         smooth_idf=True)
array_bag_1= tfidf.fit_transform(bag_1).toarray()
print(array_bag_1)

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


In [ ]:
mylist = list(array_bag_1) # converting array to list to see the each vector
print(mylist[0])

[0. 0. 0. ... 0. 0. 0.]


In [ ]:
df_cvID_skills['tf_idf_cv'] = mylist

In [ ]:
df_cvID_skills.head()   # this dataframe includes the columns of cv_id , skills, tf_idf_cv

cv_id  ...                                          tf_idf_cv
0    473  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1    900  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2   1323  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3   3748  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4   6363  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

[5 rows x 3 columns]

In [ ]:
from google.colab import files 
import io
uploaded = files.upload()

Saving job_ad_contents.xlsx to job_ad_contents.xlsx


In [ ]:
# importing job_ad_contents.xlsx
job_ad_contents_path = "job_ad_contents.xlsx"
job_ad_contents_data = pd.read_excel(job_ad_contents_path) 
job_ad_contents_df = pd.concat([job_ad_contents_data]).reset_index().drop("index", axis=1)

In [ ]:
job_ad_contents_df.head()

Unnamed: 0    JobId                                               Ilan
0           0  1870838  Makam Şoförü \r\n<ul>\r\n<li>En az 5 yıl Makam...
1           1  1676048  Şoför / Sürücü Avrupa Bölge Müdürlüğü'ne bağlı...
2           2  2141993  Şoför / Sürücü Sitil Çizgi Şirketler Grubu bün...
3           3  2175311  Şoför / Sürücü <strong>Alfred Concierge Hizmet...
4           4  2193892  Şoför / Sürücü <ul><li><span><span>Yoğun iş te...

In [ ]:
data_job_ad = job_ad_contents_df.Ilan.values.tolist() # it takes the 'Ilan' column values and make a list from it.

In [ ]:
# Tokenization and removing puntuations from values in list.
data_words_job_ad = list(sent_to_words(data_job_ad)) # data_words_job_ad is a list that inclues lists of values with cleaned form.

In [ ]:
print(data_words_job_ad[:1]) #list in list and each list includes the sentences in a row. 

[['makam', 'soforu', 'ul', 'li', 'en', 'az', 'yıl', 'makam', 'soforlugu', 'tecrubesine', 'sahip', 'li', 'li', 'diksiyonu', 'duzgun', 'iletisim', 'becerisi', 'yuksek', 'li', 'li', 'dıs', 'gorunumune', 'ozen', 'gosteren', 'li', 'li', 'ileri', 'surus', 'teknikleri', 'konusunda', 'bilgili', 've', 'deneyimli', 'li', 'li', 'sınıfı', 'surucu', 'belgesine', 'sahip', 'aktif', 'otomobil', 'kullanabilen', 'li', 'li', 'esnek', 'calısma', 'saatlerine', 'uyum', 'saglayabilecek', 'li', 'li', 'askerlik', 'hizmetini', 'tamamlamıs', 'li', 'li', 'strong', 'anadolu', 'yakasında', 'strong', 'tercihen', 'suadiye', 'nbsp', 'ikamet', 'eden', 'li', 'li', 'referans', 'verebilecek', 'li', 'ul', 'br', 'br', 'is', 'tanimi', 'ul', 'li', 'baglı', 'bulundugu', 'yonetici', 'tarafından', 'sirket', 'icinde', 've', 'dısında', 'verilen', 'tum', 'gorev', 've', 'sorumlulukları', 'ustlenebilecek', 'li', 'li', 'tahsis', 'edilen', 'aracın', 'trafik', 'kurallarına', 'uygun', 'olarak', 'kullanımına', 'ozen', 'gosterecek', 'li', 

In [ ]:
# Remove Stop Words
data_words_job_ad_nostops = remove_stopwords(data_words_job_ad)
print(data_words_job_ad_nostops[:1])

[['makam', 'soforu', 'yıl', 'makam', 'soforlugu', 'tecrubesine', 'sahip', 'diksiyonu', 'duzgun', 'iletisim', 'becerisi', 'yuksek', 'dıs', 'gorunumune', 'ozen', 'gosteren', 'ileri', 'surus', 'teknikleri', 'konusunda', 'bilgili', 'deneyimli', 'sınıfı', 'surucu', 'belgesine', 'sahip', 'aktif', 'otomobil', 'kullanabilen', 'esnek', 'calısma', 'saatlerine', 'uyum', 'saglayabilecek', 'askerlik', 'hizmetini', 'tamamlamıs', 'anadolu', 'yakasında', 'tercihen', 'suadiye', 'ikamet', 'eden', 'referans', 'verebilecek', 'is', 'tanimi', 'baglı', 'bulundugu', 'yonetici', 'tarafından', 'sirket', 'icinde', 'dısında', 'verilen', 'tum', 'gorev', 'sorumlulukları', 'ustlenebilecek', 'tahsis', 'edilen', 'aracın', 'trafik', 'kurallarına', 'uygun', 'olarak', 'kullanımına', 'ozen', 'gosterecek', 'kullanmakta', 'oldugu', 'aracın', 'periyodik', 'bakımlarının', 'zamanında', 'eksiksiz', 'bir', 'sekilde', 'yerine', 'getirilmesini', 'saglamak', 'kisisel', 'hijyen', 'temizlik', 'kurallarına', 'uyarak', 'belirtilen', 's

In [ ]:
corpus_2 =[]
for doc in data_words_job_ad_nostops: # I also didn't use the stemmed words for corpus because they are not correct.
  corpus_2.append(" ".join(doc))
print(corpus_2)

array_corpus_2 = np.array(corpus_2)

['makam soforu yıl makam soforlugu tecrubesine sahip diksiyonu duzgun iletisim becerisi yuksek dıs gorunumune ozen gosteren ileri surus teknikleri konusunda bilgili deneyimli sınıfı surucu belgesine sahip aktif otomobil kullanabilen esnek calısma saatlerine uyum saglayabilecek askerlik hizmetini tamamlamıs anadolu yakasında tercihen suadiye ikamet eden referans verebilecek is tanimi baglı bulundugu yonetici tarafından sirket icinde dısında verilen tum gorev sorumlulukları ustlenebilecek tahsis edilen aracın trafik kurallarına uygun olarak kullanımına ozen gosterecek kullanmakta oldugu aracın periyodik bakımlarının zamanında eksiksiz bir sekilde yerine getirilmesini saglamak kisisel hijyen temizlik kurallarına uyarak belirtilen standartlar cercevesinde hizmet vermek', 'sofor surucu avrupa bolge mudurlugu baglı subelerinde uzere lise mezunu aktif olarak arac kullanabilen sınıfı surucu belgesine sahip src belgesi psikoteknik raporu bulunan erkek adaylar icin askerlikle ilisigi bulunmayan 

In [ ]:
df_job_id =  job_ad_contents_df[['JobId']]
df_ilan = pd.DataFrame(corpus_2)

In [ ]:
df_jobID_ilan = pd.concat([df_job_id, df_ilan], axis=1)
df_jobID_ilan.columns = ['job_id' , 'ilanlar']

In [ ]:
df_jobID_ilan.head()  # this dataframe includes job_id and cleaned text of ilanlar(job_ad)

job_id                                            ilanlar
0  1870838  makam soforu yıl makam soforlugu tecrubesine s...
1  1676048  sofor surucu avrupa bolge mudurlugu baglı sube...
2  2141993  sofor surucu sitil cizgi sirketler grubu bunye...
3  2175311  sofor surucu alfred concierge hizmetleri turki...
4  2193892  sofor surucu yogun is temposuna esnek calısma ...

In [ ]:
# Applying countVectorizer 
count_2 = CountVectorizer()
bag_2 = count_2.fit_transform(array_corpus_2)

In [ ]:
print(count_2.vocabulary_) #A mapping of terms to feature indices.
print(count_2.get_feature_names())

{'makam': 8963, 'soforu': 12816, 'yıl': 16157, 'soforlugu': 12813, 'tecrubesine': 13842, 'sahip': 12032, 'diksiyonu': 3653, 'duzgun': 4095, 'iletisim': 6773, 'becerisi': 1625, 'yuksek': 16057, 'dıs': 4104, 'gorunumune': 5789, 'ozen': 10689, 'gosteren': 5830, 'ileri': 6749, 'surus': 13373, 'teknikleri': 13914, 'konusunda': 8260, 'bilgili': 1876, 'deneyimli': 3420, 'sınıfı': 13423, 'surucu': 13368, 'belgesine': 1693, 'aktif': 369, 'otomobil': 10614, 'kullanabilen': 8368, 'esnek': 4632, 'calısma': 2465, 'saatlerine': 11934, 'uyum': 14904, 'saglayabilecek': 11996, 'askerlik': 1102, 'hizmetini': 6485, 'tamamlamıs': 13580, 'anadolu': 649, 'yakasında': 15378, 'tercihen': 14043, 'suadiye': 13155, 'ikamet': 6697, 'eden': 4155, 'referans': 11660, 'verebilecek': 15051, 'is': 7115, 'tanimi': 13608, 'baglı': 1351, 'bulundugu': 2247, 'yonetici': 15942, 'tarafından': 13677, 'sirket': 12681, 'icinde': 6612, 'dısında': 4110, 'verilen': 15071, 'tum': 14394, 'gorev': 5748, 'sorumlulukları': 12933, 'ustle

In [ ]:
print(bag_2.toarray())
print(bag_2.shape)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
(1000, 16302)


In [ ]:
#Convert a collection of raw documents to a matrix of TF-IDF features.
tfidf_2 = TfidfTransformer(use_idf=True, 
                         norm='l2', 
                         smooth_idf=True)
print(tfidf_2.fit_transform(bag_2).toarray())

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


In [ ]:
array_bag_2= (tfidf.fit_transform(bag_2)).toarray() #rename of the above array

In [ ]:
mylist_2 = list(array_bag_2) #convert array to list to append to dataframe
df_jobID_ilan['tf_idf_job_ilan'] = mylist_2

In [ ]:
df_jobID_ilan.head() # dataframe includes jobid, ilanlar and tf_idf vectors

job_id  ...                                    tf_idf_job_ilan
0  1870838  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1  1676048  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2  2141993  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3  2175311  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4  2193892  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

[5 rows x 3 columns]

In [ ]:
from google.colab import files 
import io
uploaded = files.upload()

Saving job_ad_cv_evaluations.xlsx to job_ad_cv_evaluations.xlsx


In [ ]:
column_names = ["JobId", "CvId" , "BasvuruDurum", "Label"]
excel_path = "job_ad_cv_evaluations.xlsx"
evaluations_data = pd.read_excel(excel_path, "Sayfa2", header=None, names=column_names)
evaluations_df = pd.concat([evaluations_data]).reset_index().drop("index", axis=1)

In [ ]:
evaluations_df = evaluations_df.drop(evaluations_df.index[0])
evaluations_df = evaluations_df.drop('BasvuruDurum', 1) # I have dropped the 'BasvuruDurum' column.
evaluations_df.head()

JobId       CvId Label
1  490619   11702287     1
2  490619  100819267     1
3  490619  105843622     1
4  490619  106155661     1
5  490619  108241683     1

In [ ]:
df_cvid_dropped = df_cvID_skills.dropna() # dropped the null values if it is exist.
df_cvid_dropped.head()

cv_id  ...                                          tf_idf_cv
0    473  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1    900  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2   1323  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3   3748  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4   6363  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

[5 rows x 3 columns]

In [ ]:
# I have dropped the null values by looping over the evaluations_df dataframe because somewhat the dropna function didn't work for me.
for index, row in evaluations_df.iterrows():
  a = df_cvid_dropped.loc[df_cvid_dropped['cv_id'] == row['CvId'], 'tf_idf_cv'].values
  if(a.size==0):
    evaluations_df=evaluations_df.drop([index])

In [ ]:
# In this code section I have concatenate the tfidfs vectors of cv's and job's and put them into list.
concatenate = []
for index, row in evaluations_df.iterrows():
  a = df_cvid_dropped.loc[df_cvid_dropped['cv_id'] == row['CvId'], 'tf_idf_cv'].values
  if(a.size==0):
    continue
  else:
    a = df_cvid_dropped.loc[df_cvid_dropped['cv_id'] == row['CvId'], 'tf_idf_cv'].values[0]
    b = df_jobID_ilan.loc[df_jobID_ilan['job_id'] == row['JobId'], 'tf_idf_job_ilan'].values[0]
    c = np.concatenate((a,b), axis=None)
    concatenate.append(c) 

In [ ]:
evaluations_df['concatenated_vectors'] = concatenate # load the list to the evaluations_df.

In [ ]:
evaluations_df.head()

JobId       CvId Label                               concatenated_vectors
1  490619   11702287     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2  490619  100819267     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3  490619  105843622     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4  490619  106155661     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
5  490619  108241683     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

In [ ]:
evaluations_df = evaluations_df.drop(['JobId','CvId'], axis=1) # I have dropped the 'JobId' and 'CvId' columns.
evaluations_df.head()

Label                               concatenated_vectors
1     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
5     1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

In [ ]:
from sklearn.model_selection import train_test_split

x = evaluations_df['concatenated_vectors'].values # Features
y = evaluations_df['Label'].values  # Labels
y=y.astype('int')
x_son = np.vstack(x[:]).astype(np.float32)

x_train, x_test, y_train, y_test = train_test_split(x_son, y, test_size=0.3)


In [ ]:
#Import Random Forest Model
from sklearn.ensemble import RandomForestClassifier

#Create a Gaussian Classifier
clf=RandomForestClassifier(n_estimators=100)

#Train the model using the training sets y_pred=clf.predict(X_test)
clf.fit(x_train,y_train)

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [ ]:
y_pred=clf.predict(x_test)

In [ ]:
from sklearn.metrics import accuracy_score
print(accuracy_score(y_test, y_pred))

0.8333333333333334
